In [1]:
import pandas as pd
import numpy as np

import plotly.graph_objects as go
import plotly.express as px

from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.utils.class_weight import compute_class_weight, compute_sample_weight
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import recall_score

In [2]:
## HELPER FUNCTIONS ##
def get_prob_col(df, col, per_customer=False):
    if per_customer:
        _df = df.groupby('cust_id').first().reset_index().copy()
    else:
        _df = df.copy()
    col_item_counts = _df.groupby([col, 'label']).size().unstack(fill_value=0)

    print(_df[col].unique())

    total_pos = col_item_counts[1].sum()
    total_neg = col_item_counts[0].sum()

    pos_name = col + '_high_risk_prob'
    neg_name = col + '_low_risk_prob'

    col_item_counts[pos_name] = col_item_counts[1] / total_pos
    col_item_counts[neg_name] = col_item_counts[0] / total_neg

    col_item_counts = col_item_counts.reset_index()

    return df.merge(col_item_counts[[col, pos_name, neg_name]], on=col, how='left')

## Using Bayesian Approach

In [3]:
kyc_data = pd.read_parquet('../data/processed/kyc.parquet')
emt_data = pd.read_csv('../data/raw/emt.csv')
wire_data = pd.read_csv('../data/raw/wire.csv')
cash_data = pd.read_csv('../data/raw/cash.csv')

In [4]:
# flatten emt_data so each row is per trxn and per customer
emt_data_sender = emt_data[['cust_id_sender', 'name_sender', 'trxn_message', 'emt_value']]
emt_data_sender = emt_data_sender.rename(columns={'cust_id_sender': 'cust_id', 'name_sender': 'name', 'emt_value': 'value'})
emt_data_receiver = emt_data[['cust_id_receiver', 'name_receiver', 'trxn_message', 'emt_value']]
emt_data_receiver = emt_data_receiver.rename(columns={'cust_id_receiver': 'cust_id', 'name_receiver': 'name', 'emt_value': 'value'})
flat_emt_data = pd.concat([emt_data_sender, emt_data_receiver], ignore_index=True).reset_index(drop=True)
# remove rows where external cust_id
flat_emt_data = flat_emt_data[flat_emt_data['cust_id'].str.startswith('CUST')]
# add kyc data
# NOTE: checked that all names in flat_emt_data are in kyc_data and vice versa
flat_emt_data = flat_emt_data.drop(columns=['name']).merge(kyc_data, on='cust_id', how='left')
flat_emt_data['trxn_type'] = 'emt'
flat_emt_data.head()

cust_id            trxn_message  value                  name gender  \
0  CUST26232205  for the bike u lent me  154.0        JASON GARRISON   male   
1  CUST35533148                     NaN  518.0      ANTHONY ROBERSON   male   
2  CUST59096559                     NaN   46.0            KEVIN PARK   male   
3  CUST69049633                     NaN  570.0          ZHU FENG LAN   male   
4  CUST27403977                     NaN  480.0  IND.DAVID DUNLAP JR.  other   

                       occupation   age  tenure  occ_wealth  occ_animal  \
0                         Luthier  32.0    13.0           0           0   
1                        Hotelier  48.0    18.0           0           0   
2    Import/Export Business Owner  34.0     8.0           1           0   
3              Retail Salesperson  35.0     0.0           0           0   
4  Private Security Company Owner  69.0    14.0           1           0   

   occ_int  label trxn_type  
0        0      0       emt  
1        0      0       emt  
2        1      0       emt  
3        0      0       emt  
4        1      0       emt

In [5]:
wire_data

cust_id_sender cust_id_receiver           name_sender  \
0      EXTERNAL753550     CUST30139466              CHEN MIN   
1        CUST43146787     CUST94438297  DR. BENJAMÍN PAREDES   
2        CUST82396415   EXTERNAL842611        WHITNEY WRIGHT   
3      EXTERNAL851271     CUST84545757        DR.TRACY MOODY   
4      EXTERNAL685849     CUST14982223          JEREMY WHITE   
...               ...              ...                   ...   
67867    CUST89899937   EXTERNAL470484      ÉLISABETH BENOÎT   
67868    CUST59834819   EXTERNAL634239          EMMA RICHARD   
67869    CUST49543616   EXTERNAL147586          THOMAS EVANS   
67870    CUST31344256     CUST78691452        DR. JANET DIAZ   
67871  EXTERNAL583238     CUST30882369        JOHNATHAN HALL   

          name_receiver  trxn_value country_sender country_receiver  \
0         DESTINY MOORE     10098.0             CN               CA   
1         BOBBY SERRANO      1267.0             CA               CA   
2        VICTORIA HOGAN      8591.0             CA               US   
3         MINDY BURGESS      1480.5             CA               CA   
4         NITARA BARMAN     13310.0             AU               CA   
...                 ...         ...            ...              ...   
67867   DANIEL SHEPPARD      5067.0             CA               CA   
67868          WANG HUA     18874.0             CA               CN   
67869     ANNE THOMPSON      1034.5             CA               US   
67870   TIMOTHY BENNETT      4084.0             CA               CA   
67871  ISABELLE DELISLE      1542.0             CA               CA   

            trxn_id  
0      TKEV83070517  
1      LWCS42954834  
2      NTTG55749308  
3      IXVD84599097  
4      TIGB41956889  
...             ...  
67867  KVQK50168638  
67868  IUIP17370739  
67869  SYRW79049777  
67870  ZHVK78574815  
67871  YJNY79150994  

[67872 rows x 8 columns]

In [6]:
# flatten wire_data so each row is per trxn and per customer
wire_data_sender = wire_data[['cust_id_sender', 'name_sender', 'trxn_value', 'country_receiver']]
wire_data_sender = wire_data_sender.rename(columns={'cust_id_sender': 'cust_id', 'name_sender': 'name', 'country_receiver': 'country_other', 'trxn_value': 'value'})
wire_data_receiver = wire_data[['cust_id_receiver', 'name_receiver', 'trxn_value', 'country_sender']]
wire_data_receiver = wire_data_receiver.rename(columns={'cust_id_receiver': 'cust_id', 'name_receiver': 'name', 'country_sender': 'country_other', 'trxn_value': 'value'})
flat_wire_data = pd.concat([wire_data_sender, wire_data_receiver], ignore_index=True).reset_index(drop=True)

# remove rows where external cust_id
flat_wire_data = flat_wire_data[flat_wire_data['cust_id'].str.startswith('CUST')]

# add kyc data
# NOTE: checked that all names in flat_wire_data are in kyc_data and vice versa
flat_wire_data = flat_wire_data.drop(columns=['name']).merge(kyc_data, on='cust_id', how='left')
flat_wire_data['trxn_type'] = 'wire'
flat_wire_data.head()

cust_id   value country_other                  name  gender  \
0  CUST43146787  1267.0            CA  DR. BENJAMÍN PAREDES  female   
1  CUST82396415  8591.0            US        WHITNEY WRIGHT  female   
2  CUST61153056  1587.0            CA       DUANE HENDERSON    male   
3  CUST93918261  1546.0            CA        VINCENT BÉDARD    male   
4  CUST13916601  2503.5            CA          KENNETH TODD    male   

                                    occupation   age  tenure  occ_wealth  \
0                                    Architect  34.0     0.0           0   
1  Freelancer (e.g., Graphic Designer, Writer)  38.0     5.0           0   
2                                      Student  22.0     3.0           0   
3                                        Baker  36.0     0.0           0   
4                  Private Equity Fund Manager  48.0    16.0           1   

   occ_animal  occ_int  label trxn_type  
0           0        0      0      wire  
1           0        0      1      wire  
2           0        0      0      wire  
3           0        0      1      wire  
4           0        1      1      wire

In [7]:
flat_cash_data = cash_data.drop(columns=['trxn_id']).merge(kyc_data, on='cust_id', how='left')
flat_cash_data = flat_cash_data.rename(columns={'trxn_amount': 'value'})
flat_cash_data['trxn_type'] = 'cash'
flat_cash_data.head()

cust_id  value        type                 name  gender  \
0  CUST69827909   2330     deposit       THERESA JACOBS  female   
1  CUST78509707   4800     deposit  LUCY-OCÉANE VINCENT  female   
2  CUST71480951   6510  withdrawal         PRISHA BALAN    male   
3  CUST70854140   1715     deposit       CHENG HONG XIA    male   
4  CUST57406487   3770  withdrawal          MIKE HANSON   other   

          occupation   age  tenure  occ_wealth  occ_animal  occ_int  label  \
0            Unknown  62.0     1.0           0           0        0      0   
1  Real Estate Agent  33.0     0.0           1           0        1      0   
2              Other  32.0     3.0           0           0        0      0   
3              Other  38.0     4.0           0           0        0      0   
4          Carpenter  36.0     8.0           0           0        0      0   

  trxn_type  
0      cash  
1      cash  
2      cash  
3      cash  
4      cash

In [8]:
full_df = pd.concat([flat_emt_data, flat_wire_data, flat_cash_data], ignore_index=True).reset_index(drop=True)
full_df

cust_id            trxn_message    value                  name  \
0        CUST26232205  for the bike u lent me    154.0        JASON GARRISON   
1        CUST35533148                     NaN    518.0      ANTHONY ROBERSON   
2        CUST59096559                     NaN     46.0            KEVIN PARK   
3        CUST69049633                     NaN    570.0          ZHU FENG LAN   
4        CUST27403977                     NaN    480.0  IND.DAVID DUNLAP JR.   
...               ...                     ...      ...                   ...   
1003060  CUST78377468                     NaN   7865.0          KARTIK KAKAR   
1003061  CUST82786181                     NaN   2770.0           JAIME CLINE   
1003062  CUST30355964                     NaN   7495.0        DANIELLE LOGAN   
1003063  CUST95759935                     NaN  19290.0        CRAIG MITCHELL   
1003064  CUST66182718                     NaN  26175.0         JULIA ROBERTS   

         gender                                   occupation   age  tenure  \
0          male                                      Luthier  32.0    13.0   
1          male                                     Hotelier  48.0    18.0   
2          male                 Import/Export Business Owner  34.0     8.0   
3          male                           Retail Salesperson  35.0     0.0   
4         other               Private Security Company Owner  69.0    14.0   
...         ...                                          ...   ...     ...   
1003060  female  Freelancer (e.g., Graphic Designer, Writer)  45.0     5.0   
1003061    male                                Notary Public  68.0    18.0   
1003062  female                         Import/Export Dealer  44.0     4.0   
1003063    male                                  Taxi Driver  48.0     4.0   
1003064  female                       Nightclub or Bar Owner  46.0     5.0   

         occ_wealth  occ_animal  occ_int  label trxn_type country_other  \
0                 0           0        0      0       emt           NaN   
1                 0           0        0      0       emt           NaN   
2                 1           0        1      0       emt           NaN   
3                 0           0        0      0       emt           NaN   
4                 1           0        1      0       emt           NaN   
...             ...         ...      ...    ...       ...           ...   
1003060           0           0        0      0      cash           NaN   
1003061           0           0        0      0      cash           NaN   
1003062           1           0        1      0      cash           NaN   
1003063           0           0        0      0      cash           NaN   
1003064           1           0        0      0      cash           NaN   

               type  
0               NaN  
1               NaN  
2               NaN  
3               NaN  
4               NaN  
...             ...  
1003060     deposit  
1003061  withdrawal  
1003062  withdrawal  
1003063     deposit  
1003064     deposit  

[1003065 rows x 15 columns]

In [9]:
# Get conditional probabilities for desired columns
full_df = get_prob_col(full_df, 'trxn_type')
full_df = get_prob_col(full_df, 'type')
full_df = get_prob_col(full_df, 'value')
full_df = get_prob_col(full_df, 'country_other')
full_df = get_prob_col(full_df, 'gender', per_customer=True)
full_df = get_prob_col(full_df, 'tenure', per_customer=True)
full_df = get_prob_col(full_df, 'age', per_customer=True)
full_df = get_prob_col(full_df, 'occupation', per_customer=True)
full_df = get_prob_col(full_df, 'occ_wealth', per_customer=True)
full_df = get_prob_col(full_df, 'occ_animal', per_customer=True)
full_df = get_prob_col(full_df, 'occ_int', per_customer=True)
full_df.head()

['emt' 'wire' 'cash']
[nan 'deposit' 'withdrawal']
[  154.   518.    46. ... 17095. 19290. 26175.]
[nan 'CA' 'US' 'RU' 'UK' 'CN' 'GE' 'MX' 'AU' 'IN' 'SA']
['male' 'female' 'other']
[ 1. 17.  5. 16.  0.  6.  8. 13. 12.  7. 11. 14. 27. 10.  9. 32. 15.  4.
  2. 21. 20. 22.  3. 24. 19. 31. 25. 18. 26. 28. 23. 30. 35. 34. 33. 29.
 36. 37. 39. 42. 38. 43. 44. 45. 40. 41. 49. 46. 48.]
[27. 52. 37. 45. 18. 26. 46. 30. 36. 50. 33. 57. 31. 51. 39. 38. 49. 25.
 34. 29. 23. 58. 32. 35. 43. 59. 65. 42. 41. 24. 40. 68. 67. 28. 55. 56.
 63. 44. 22. 48. 21. 75. 54. 20. 60. 47. 69. 53. 74. 19. 62. 64. 73. 70.
 61. 72. 76. 82. 66. 79. 71. 80. 77. 78. 88. 86. 81. 91. 84. 83. 92. 87.
 89. 85. 90.]
['Barista' 'Civil Servant' 'Author' 'Electrician' 'Student'
 'Real Estate Agent' 'Banker' 'Paramedic' 'Journalist' 'Animal Trainer'
 'Offshore Investment Advisor' 'Fitness Trainer' 'Travel Agency Owner'
 'Wedding Planner' 'Bus Driver' 'Pastry Chef' 'Chemist' 'Hotelier'
 'Florist' 'Bartender' 'Property Manager' '

cust_id            trxn_message  value                  name gender  \
0  CUST26232205  for the bike u lent me  154.0        JASON GARRISON   male   
1  CUST35533148                     NaN  518.0      ANTHONY ROBERSON   male   
2  CUST59096559                     NaN   46.0            KEVIN PARK   male   
3  CUST69049633                     NaN  570.0          ZHU FENG LAN   male   
4  CUST27403977                     NaN  480.0  IND.DAVID DUNLAP JR.  other   

                       occupation   age  tenure  occ_wealth  occ_animal  ...  \
0                         Luthier  32.0    13.0           0           0  ...   
1                        Hotelier  48.0    18.0           0           0  ...   
2    Import/Export Business Owner  34.0     8.0           1           0  ...   
3              Retail Salesperson  35.0     0.0           0           0  ...   
4  Private Security Company Owner  69.0    14.0           1           0  ...   

   age_high_risk_prob  age_low_risk_prob occupation_high_risk_prob  \
0            0.025087           0.037845                  0.000183   
1            0.031313           0.015936                  0.013001   
2            0.033693           0.039220                  0.019227   
3            0.031313           0.039042                  0.002197   
4            0.001648           0.001185                  0.009522   

  occupation_low_risk_prob occ_wealth_high_risk_prob  \
0                 0.001304                  0.481963   
1                 0.008332                  0.481963   
2                 0.000842                  0.518037   
3                 0.014134                  0.481963   
4                 0.000539                  0.518037   

   occ_wealth_low_risk_prob  occ_animal_high_risk_prob  \
0                  0.860669                   0.991577   
1                  0.860669                   0.991577   
2                  0.139331                   0.991577   
3                  0.860669                   0.991577   
4                  0.139331                   0.991577   

   occ_animal_low_risk_prob  occ_int_high_risk_prob  occ_int_low_risk_prob  
0                  0.955619                0.575536                 0.9134  
1                  0.955619                0.575536                 0.9134  
2                  0.955619                0.424464                 0.0866  
3                  0.955619                0.575536                 0.9134  
4                  0.955619                0.424464                 0.0866  

[5 rows x 37 columns]

In [10]:
# add per customer number of total transactions, mean transaction amount, and max transaction amount
tx_stats = full_df.groupby('cust_id')['value'].agg(['count', 'mean', 'max'])
tx_stats.columns = ['num_tx', 'avg_tx_amount', 'max_tx_amount']

full_df = full_df.merge(tx_stats, on='cust_id', how='left')

full_df.head(10)

cust_id                           trxn_message  value  \
0  CUST26232205                 for the bike u lent me  154.0   
1  CUST35533148                                    NaN  518.0   
2  CUST59096559                                    NaN   46.0   
3  CUST69049633                                    NaN  570.0   
4  CUST27403977                                    NaN  480.0   
5  CUST76959536  Your old PlayStation from the listing  100.0   
6  CUST65275585                                    NaN  735.0   
7  CUST95489575                                    NaN  209.0   
8  CUST17422161                                    NaN   60.0   
9  CUST43516538                                    NaN  298.0   

                      name  gender                      occupation   age  \
0           JASON GARRISON    male                         Luthier  32.0   
1         ANTHONY ROBERSON    male                        Hotelier  48.0   
2               KEVIN PARK    male    Import/Export Business Owner  34.0   
3             ZHU FENG LAN    male              Retail Salesperson  35.0   
4     IND.DAVID DUNLAP JR.   other  Private Security Company Owner  69.0   
5                  BAI JUN   other                   Postal Worker  18.0   
6  EDUARDO PONCE VILLAREAL  female                       Architect  44.0   
7              MARY HARPER  female                    Chiropractor  27.0   
8                  LIU KUN    male                     Auto Dealer  37.0   
9        DR.JAMES CHAMBERS    male                  Animal Trainer  34.0   

   tenure  occ_wealth  occ_animal  ...  occupation_low_risk_prob  \
0    13.0           0           0  ...                  0.001304   
1    18.0           0           0  ...                  0.008332   
2     8.0           1           0  ...                  0.000842   
3     0.0           0           0  ...                  0.014134   
4    14.0           1           0  ...                  0.000539   
5     0.0           0           0  ...                  0.006993   
6    14.0           0           0  ...                  0.010643   
7     9.0           0           0  ...                  0.005505   
8     1.0           0           0  ...                  0.008291   
9     2.0           0           1  ...                  0.002803   

   occ_wealth_high_risk_prob occ_wealth_low_risk_prob  \
0                   0.481963                 0.860669   
1                   0.481963                 0.860669   
2                   0.518037                 0.139331   
3                   0.481963                 0.860669   
4                   0.518037                 0.139331   
5                   0.481963                 0.860669   
6                   0.481963                 0.860669   
7                   0.481963                 0.860669   
8                   0.481963                 0.860669   
9                   0.481963                 0.860669   

  occ_animal_high_risk_prob occ_animal_low_risk_prob  occ_int_high_risk_prob  \
0                  0.991577                 0.955619                0.575536   
1                  0.991577                 0.955619                0.575536   
2                  0.991577                 0.955619                0.424464   
3                  0.991577                 0.955619                0.575536   
4                  0.991577                 0.955619                0.424464   
5                  0.991577                 0.955619                0.424464   
6                  0.991577                 0.955619                0.575536   
7                  0.991577                 0.955619                0.575536   
8                  0.991577                 0.955619                0.575536   
9                  0.008423                 0.044381                0.575536   

   occ_int_low_risk_prob  num_tx  avg_tx_amount  max_tx_amount  
0                 0.9134       3     261.000000          611.0  
1                 0.9134       8    1747.875000         4720.0  
2 

In [11]:
# bar chart of occupation_high_risk_prob
fig = go.Figure()
high_risk_occupations = full_df[full_df['occupation_high_risk_prob'] > 0.01]['occupation'].unique()
_df = full_df[full_df['occupation'].isin(high_risk_occupations)]
fig.add_trace(go.Bar(x=_df['occupation'].unique(), y=_df['occupation_high_risk_prob'].unique(), name='High Risk'))
fig.add_trace(go.Bar(x=_df['occupation'].unique(), y=_df['occupation_low_risk_prob'].unique(), name='Low Risk'))
fig.update_layout(
    barmode='group',
    title='Occupation Risk Probabilities',
    yaxis_title='Probability'
)


In [12]:
fig = go.Figure()
_df = full_df.groupby('cust_id').first().reset_index()
fig.add_trace(go.Bar(x=_df['tenure'].unique(), y=_df['tenure_high_risk_prob'].unique(), name='High Risk'))
fig.add_trace(go.Bar(x=_df['tenure'].unique(), y=_df['tenure_low_risk_prob'].unique(), name='Low Risk'))
fig.update_layout(
    barmode='group',
    title='Tenure Risk Probabilities',
    yaxis_title='Probability'
)
fig.show()

In [21]:
# do the same with avg_tx_amount
fig = go.Figure()
_df = full_df.groupby('cust_id').first().reset_index()
# ignore average transactions below 500$
_df = _df[(_df['avg_tx_amount'] > 500) & (_df['avg_tx_amount'] < 20000)]
_df_high = _df[_df['label'] == 1]
_df_low = _df[_df['label'] == 0]

fig.add_trace(go.Histogram(x=_df_high['avg_tx_amount'], name='High Risk', histnorm='probability'))
fig.add_trace(go.Histogram(x=_df_low['avg_tx_amount'], name='Low Risk', histnorm='probability'))
fig.update_layout(
    title='Average Transaction Amount Distribution',
    xaxis_title='Average Transaction Amount',
    yaxis_title='Probability'
)

In [22]:
df = full_df.drop(columns=['cust_id', 'name', 'trxn_message']).copy()

# Identify object-type columns
categorical_cols = df.select_dtypes(include=['object']).columns
label_encoders = {}

# Apply Label Encoding to each categorical column
for col in categorical_cols:
    # if col not in ['tx_message', 'cust_id', 'trxn_id', 'Name']:  # Exclude non-feature columns
    df[col] = LabelEncoder().fit_transform(full_df[col].astype(str))

# Separate the features and the target variable
X = df.drop('label', axis=1)  # Drop the label column to create the feature set
y = df['label']  # Use the label column as the target variable

# Split the dataset into training set and test set
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

class_weights = compute_sample_weight('balanced', y=y_train)

# calculate scale_pos_weight
scale_pos_weight = len(y_train[y_train == 0]) / len(y_train[y_train == 1])

# Initialize the XGBoost classifier
# xgb_model = XGBClassifier()
xgb_model = XGBClassifier(scale_pos_weight=scale_pos_weight)

# Train the model with the training data
xgb_model.fit(X_train, y_train)

# Predict the labels for the test set
y_pred = xgb_model.predict(X_test)

# Calculate the accuracy of the model
accuracy = accuracy_score(y_test, y_pred)

print(f"Accuracy: {accuracy * 100.0}%")

Accuracy: 91.23486513835095%


In [23]:
from xgboost import plot_importance
import matplotlib.pyplot as plt

# After your model is trained:
plot_importance(xgb_model, max_num_features=20)  # Change the number as needed
plt.show()

In [24]:
# Assuming y_test are the true labels and y_pred are the predictions from the model
recall_label_1 = recall_score(y_test, y_pred, pos_label=1)
print(f'Recall for label 1: {recall_label_1}')

recall_label_0 = recall_score(y_test, y_pred, pos_label=0)
print(f'Recall for label 0: {recall_label_0}')

Recall for label 1: 0.9457697878503877
Recall for label 0: 0.9079197692207814


In [28]:
y_df = pd.DataFrame({'true_label': y_test, 'predicted_label': y_pred})

# convert the predicted label to a string ("High", "Low")
y_df['predicted_label'] = y_df['predicted_label'].apply(lambda x: 'High' if x == 1 else 'Low')
y_df['true_label'] = y_df['true_label'].apply(lambda x: 'High' if x == 1 else 'Low')

fig = go.Figure()

fig.add_trace(go.Histogram(
    x=y_df['true_label'],
    histnorm='percent',
    name='True Label',
    marker_color='rgba(55, 128, 191, 0.7)',  # Adjust the color and opacity as needed
    xbins=dict(  # bins used for histogram
        size=0.5
    ),
))

fig.add_trace(go.Histogram(
    x=y_df['predicted_label'],
    histnorm='percent',
    name='Predicted Label',
    marker_color='rgba(219, 64, 82, 0.7)',  # Adjust the color and opacity as needed
    xbins=dict(  # bins used for histogram
        size=0.5
    ),
))

# Update the layout for a sleek design
fig.update_layout(
    title_text='True vs. Predicted Labels Distribution',  # Chart title
    xaxis_title_text='Label',  # x-axis label
    yaxis_title_text='Percentage (%)',  # y-axis label with percentage sign
    bargap=0.1,  # Reduced gap between bars for a less wide appearance
    plot_bgcolor='white',  # Background color for the plot
    font=dict(
        family="Arial, sans-serif",  # Set the font type
        size=12,  # Set the font size
        color="black"  # Set the font color
    ),
    legend=dict(
        title_text='',  # Legend title
        orientation='h',  # Horizontal orientation
        yanchor="bottom",
        y=1.02,
        xanchor="right",
        x=1
    )
)

fig.update_xaxes(showgrid=False, linecolor='lightgrey')  # x-axis line color
fig.update_yaxes(showgrid=True, gridwidth=1, gridcolor='lightgrey')  # y-axis grid line color and width

fig.update_layout(width=600)
fig.show()